# Batch Lamda1050 jump correction script and smoothing

### Author: Vinicio Soto, CICIMA
### This script works with raw Lambdas1050's ASC files in batch. It corrects Lambdas1050's detector jump between 857 nm and 858 nm and performs a Savitzky-Golay filtering on the corrected data

### Dependencies

In [1]:
import pandas as pd
import numpy as np
from matplotlib.backends.backend_pdf import PdfPages
import matplotlib
import matplotlib.pyplot as plt
import os
import re

### Instructions:

Write your archive folders' path in file_folder_data_path list

In [2]:
#Lists all archives in folder
file_folder_data_path =[ r"C:\Users\EstebanSoto\Downloads\VINICIO\VINICIO\2023-03-CICIMAUCR-2-REFLECTANCE",
                       r"C:\Users\EstebanSoto\Downloads\VINICIO\VINICIO\2024-03_ANGSOL-REFLECTANCE\ASC",
                       r"C:\Users\EstebanSoto\Downloads\VINICIO\VINICIO\2024-01_CICIMAUCR-REFLECTANCE\ASC",
                        r"C:\Users\EstebanSoto\Downloads\VINICIO\VINICIO\2024-02_INBUCRREFLECTANCE\New names\ASC",
                        r"C:\Users\EstebanSoto\Downloads\VINICIO\VINICIO\2023-11-TRANSFLECTANCE_AND_TRANSMITTANCE\new names\transmittance\Modificado\ASC",
                        r"C:\Users\EstebanSoto\Downloads\VINICIO\VINICIO\2023-11-TRANSFLECTANCE_AND_TRANSMITTANCE\new names\transflectance\Modificado\ASC",
                       r"C:\Users\EstebanSoto\Downloads\VINICIO\VINICIO\2024_02_BIOUCR-REFLECTANCE\ASC",
                       ]

#determine 
markersize = 1

### Functions

In [3]:
def get_metadata_and_dataframe(file_location):
    """This function reads L1050 .ASC files directly and returns a dictionary with metadata and the dataframe with the measurements"""
    import os
    import pandas as pd
    import re

    def get_sample_code_from_filename(row_str, file_location):
        #print("string")
        #print(file_location)
        filename = os.path.basename(file_location)
        re1 = r"([a-zA-Z\d]+)(?:-\d)*(?:.Sample)*.(?:txt)*(?:ASC)*"
        #Names are in the form CODE-MEASUREMENTNUMBER.TXT
        p = re.compile(re1)
        m = p.match(filename)
        # print(f"match filename: {m}")
        if m:
            # print(f"group 1: {m.group(1)}")
            return(m.group(1))
        return get_sample_code(file_str)

    def get_sample_code(row_str):
        #Tries to get the sample code from the file, if it does not match
        #it tries to get it from the filename.
        # print("string")
        # print(row_str)
        re1 = r"([a-zA-Z\d]+)(?:-\d)*(?:.Sample)*.(?:txt)*(?:ASC)*"
        #Names are in the form CODE-MEASUREMENTNUMBER.TXT
        p = re.compile(re1)
        m = p.match(row_str)
        # print(f"match: {m}")
        if m:
            return(m.group(1))
        else:
            ""

    def responses(str):
        re1 = "\d+/(\d+,\d+) \d+,\d+/(\d+,\d+)"
        p = re.compile(re1)
        m= p.match(str)
        if m:
            return m.group(1),m.group(2)
        else:
            return "",""
    def attenuator_settings(str):
        re1 = "S:(\d+,\d+) R:(\d+,\d+)"
        p = re.compile(re1)
        m= p.match(str)
        if m:
            return m.group(1),m.group(2)
        else:
            return "",""
    def slit_pmt_aperture(str):
        re1 = "\d+/servo \d+,\d+/(\d+,\d+)"
        p = re.compile(re1)
        m= p.match(str)
        if m:
            return m.group(1)
        else:
            return ""
    #Initializa metadata dict
    metadata = {}

    #Read header
    lines = []
    with open(file_location, encoding= "latin1") as myfile:
        lines = myfile.readlines()[0:90]
    metadata["header"] = "".join(lines)


    #read_metadata
    f = open(file_location, encoding= "latin1")

    df = pd.DataFrame()
    with f as data_file:
        for index, row in enumerate(data_file): #0-89

            row_str = row.strip()
            if index +1 == 3: #Filename and extension
                metadata["filename"]= row_str
                metadata["code"] = get_sample_code_from_filename(row_str, file_location)
            if index + 1 == 4: #date DD/MM/YYYY
                metadata["date"]= row_str
            if index + 1 == 5:#Time HH:MM:SS.SS
                metadata["time"]= row_str
            if index + 1 == 8:#user
                metadata["user"]= row_str
            if index + 1 == 9:#description
                metadata["description"]= row_str
            if index + 1 == 10:#minimum wavelength
                metadata["minimum_wavelength"]= row_str
            if index + 1 == 12:#equipment name
                metadata["equipment"]= row_str
            if index + 1 == 13:#equipment series
                metadata["series"]= row_str
            if index + 1 == 14:#data visualizer version, equipment version, date and time
                metadata["software"]= row_str
            if index + 1 == 21:#Operating mode
                metadata["operating_mode"]= row_str
            if index + 1 == 22: #Number of cycles
                metadata["cycles"]= row_str
            if index + 1 == 32: #range/servo
                metadata["slit_pmt"]= slit_pmt_aperture(row_str)
            if index + 1 == 33:
                metadata["response_ingaas"], metadata["response_pmt"]= responses(row_str)
            if index + 1 == 35: #pmt gain, if 0 is automatic
                metadata["pmt_gain"]= row_str
            if index + 1 == 36: #InGaAs detector gain
                metadata["ingaas_gain"]= row_str
            if index + 1 == 42:#monochromator wavelength nm
                metadata["monochromator_change"]= row_str
            if index + 1 == 43:#lamp change wavelength
                metadata["lamp_change"]= row_str
            if index + 1 == 44:#pmt wavelength
                metadata["pmt_change"]= row_str
            if index + 1 == 45:#beam selector
                metadata["beam_selector"]= row_str
            if index + 1 == 46:
                metadata["cbm"]= row_str
            if index + 1 == 47: #cbd status, on/off
                metadata["cbd_status"]= row_str
            if index + 1 == 48: #attenuator percentage
                metadata["attenuator_sample"], metadata["attenuator_reference"]= attenuator_settings(row_str)
            if index + 1 == 49:
                metadata["polarizer"]= row_str
            if index + 1 == 80:
                metadata["units"]= row_str
            if index + 1 == 81:
                metadata["measuring_mode"]= row_str
            if index + 1 == 84:
                metadata["maximum_wavelength"]= row_str
            if index + 1 == 85:
                metadata["step"]= row_str
            if index + 1 == 86:
                metadata["number_of_datapoints"]= row_str
            if index + 1 == 88:
                metadata["maximum_measurement"]= row_str
            if index + 1 == 89:
                metadata["minimum_measurement"]= row_str
            if index +1 == 90:
                break
        df = pd.read_csv(f, sep="\t", decimal =",", names=["wavelength", metadata["measuring_mode"]]).dropna()
        
        df["wavelength"],df[metadata["measuring_mode"]] = df["wavelength"].astype(float), df[metadata["measuring_mode"]].astype(float)
        return metadata, df

### Correction process function

In [4]:
def jump_correction(file_folder_data_path, filename, metadata):
    #measuring_mode
    measuring_mode = metadata["measuring_mode"]
    
    #constants
    markersize = 1 #Marker size for plots

    # read text file into pandas DataFrame 
    full_path= file_folder_data_path + "\\" + filename
    
    #Read header
    lines = []
    with open(full_path) as myfile:
        lines = myfile.readlines()[0:90] 
    header = "".join(lines)

    #read body
    f = open(full_path)
    df = pd.read_csv(f, sep="\t", decimal = ",", skiprows=90,  
                     names=["wavelength", measuring_mode])
    
    #convert columns to float
    df['wavelength'] = df['wavelength'].astype(float)
    df[measuring_mode] = df[measuring_mode].astype(float)
    

    #This code finds the rows before and after the detector change
    #freq1 is the frequency before the change and freq2 is the frequency after the change
    wavelenght1 = 857.000000 #857
    wavelenght2 = 858.000000 #858
    
    #print("Loc")
    row1 = df.loc[ df['wavelength'] == wavelenght1]
    row2 = df.loc[ df['wavelength'] == wavelenght2]
    row22 = df.loc[ df['wavelength'] == wavelenght2 +1]
    row23 = df.loc[ df['wavelength'] == wavelenght2+2]
    row24 = df.loc[ df['wavelength'] == wavelenght2+3]
    row25 = df.loc[ df['wavelength'] == wavelenght2+4]
    
    #This code finds the values corresponding to those frequencies and creates a correction factor
    
    try:
        data1 = row1.iat[0,1]
        data2 = row2.iat[0,1]
        data22 = row22.iat[0,1]
        data23 = row23.iat[0,1]
        data24 = row23.iat[0,1]
        data25 = row23.iat[0,1]
    
        data2_avg = (data2 + data22+data23+data24+data25)/5
    
        correction_factor= data2_avg/data1 
    
        #Multiply all frequencies equal or greater than freq2 by correction_factor
        df2 = df
        df2.loc[df2["wavelength"] <= wavelenght2 -1, [measuring_mode]] *= correction_factor

        #SAVE FILES
        #convert dataframe to numpy
        my_numpy_df_data = df.to_numpy()
        
        #Create new folder
        #corrected_path = file_folder_data_path + "\\jump_corrected_files\\"
        corrected_path = os.path.join(file_folder_data_path , "jump_corrected_files")
        
        if not os.path.exists(corrected_path):
            os.mkdir(corrected_path)
            
        #saves file, removes .ASC and removes .SAMPLE
        unnecessary_text = [".Sample", ".Cycle1"]
        temp_text = filename.replace('.ASC', ''+'.txt')
        for text in unnecessary_text:
            #print(temp_text)
            temp_text = temp_text.replace(text, "")
        
        #new_archive_name = corrected_path + temp_text
        new_archive_name = os.path.join(corrected_path , temp_text)
        
        with open(new_archive_name, 'wb') as f:
            np.savetxt(new_archive_name, my_numpy_df_data,fmt = "%.6f", delimiter="\t", header=header, comments='', )
        with open(new_archive_name, "r") as f:
            data = f.read()
        with open(new_archive_name, "w") as f:
            f.write(data.replace("#DATA\n","#DATA"))
        return df
    except Exception as e:
        
        print(e)
        return pd.DataFrame([])
    
    

In [5]:
from scipy.signal import savgol_filter

def savitzky_golay_filter(metadata, df) -> pd.DataFrame:
    measuring_mode = metadata["measuring_mode"]
    y = df[measuring_mode] = df[measuring_mode].astype(float)
    
    # Apply Savitzky-Golay filter
    window_length = 15  # Window length (odd number)
    polyorder = 3  # Polynomial order
    y_smooth = savgol_filter(y, window_length, polyorder)
    
    #create new dataframe
    df_smooth = pd.DataFrame([])
    df_smooth["wavelength"] =df["wavelength"]
    df_smooth[measuring_mode] = y_smooth
    
    return df_smooth
    

In [6]:
def filter_list_extension(file_folder_data_path):
    file_list = os.listdir(file_folder_data_path)

    #file extension
    file_extension = ".ASC"

    # filters a list of strings to create a new list containing only the elements that end with ".ASC"

    def filter_substring_elements(path_strings, substring):
        filtered_paths = [path for path in path_strings if substring in path]
        return filtered_paths

    # Filtering elements ending with ".ASC"
    filtered_list = filter_substring_elements(file_list, file_extension)

    # Displaying the filtered list
    #print(filtered_list)
    
    return filtered_list

### Logic: Remove jumps

In [7]:
#for each folder location:
file_counter = 0

for folder in file_folder_data_path:
    
    filtered_list = filter_list_extension(folder)
    #create a subfolder called report with the correction process info  
    report_path = os.path.join(folder, "report")  

    if not os.path.exists(report_path):
            os.mkdir(report_path)

    new_file = os.path.join( report_path , 'spectra_average_report.pdf')
    
    #create a report in pdf
    with matplotlib.backends.backend_pdf.PdfPages(new_file) as pdf:

        for file in filtered_list:
            #obtain metadata
            metadata, df = get_metadata_and_dataframe(folder + "//"+file)
            filename = metadata["filename"]
            
            #create figure
            plt.figure(figsize=(10, 4))
            #plots before changes
            #plt.subplot(1, 2, 1)  # 1 row, 2 columns, subplot 1
            plt.plot(df["wavelength"], df[metadata["measuring_mode"]], color = "r")
            plt.title(f'1. Raw data. {filename}')
            pdf.savefig()
            plt.close()

            #Fix jump correction
            df_corrected = jump_correction(folder, file, metadata)

            #print(df_corrected)
            #plots changes
            if not df_corrected.empty:
                #plt.subplot(1, 2, 2)
                plt.figure(figsize=(10, 4))
                plt.plot(df_corrected["wavelength"], df_corrected[metadata["measuring_mode"]], color = "y")
                plt.title(f'2: Jump correction.  {filename}')
                #plt.show()
                pdf.savefig()
                plt.close()

                #filter data
                df_smooth = savitzky_golay_filter(metadata, df_corrected)
                plt.figure(figsize=(10, 4))
                plt.plot(df_smooth["wavelength"], df_smooth[metadata["measuring_mode"]], color = "g")
                plt.title(f'3: Savitzky-Golay filtering.  {filename}')
                #plt.show()
                pdf.savefig()
                plt.close()
                
                file_counter = file_counter + 1

            #Show comparison
            #plt.tight_layout()  # Adjust layout to prevent overlap
print(f"{file_counter} files were corrected")

index 0 is out of bounds for axis 0 with size 0
433 files were corrected


In [8]:
#calculate averages

In [9]:
def get_files_with_same_name(directory):
    #get files in directory
    files = os.listdir(directory)
    
    sample_names = []
    re1 = r"([a-zA-Z\d]+)(?:-\d)*(?:.Sample)*.(?:txt)*(?:ASC)*"
    #Names are in the form CODE-MEASUREMENTNUMBER.TXT
    for file in files:
        #print(file)
        p = re.compile(re1)
        m = p.match(file)
        if m:
            sample_names.append(m.group(1))

    return set(sample_names)

In [10]:
def average_files(code_set, directory):
    
    #parent directory
    save_directory = os.path.dirname(directory)
    
    print(f"{save_directory=}")
    
    for code in code_set:
        print(f"{code=}")
        files = [file for file in os.listdir(directory) if file.endswith('.txt') 
                 and "fail" not in file 
                 and "test" not in file
                 and len(file)]
        
        #print(files)
        
        # Create an empty list to store dataframes
        dataframes = []

        # Read each file, create dataframes, and plot them
        for file in files:
            print(f"{file=}")
            #file path
            file_path = os.path.join(directory, file)

            #get metadata and dataframe
            metadata, df = get_metadata_and_dataframe(file_path)

            #metadata info
            measuring_mode = metadata["measuring_mode"]
            sample_name = metadata["code"] 

            # Read the file into a pandas DataFrame

            #convert columns to float
            df['wavelength'] = df['wavelength'].astype(float)
            df[measuring_mode] = df[measuring_mode].astype(float)
            
            # Append the dataframe to the list
            dataframes.append(df)
            
            #print(df)

        # Calculate the average of all dataframes
        average_df = pd.concat(dataframes).groupby('wavelength').mean().reset_index()
        std_dev_df = pd.concat(dataframes).groupby('wavelength').std().reset_index()

        print(f"{average_df=}")
        
        #standard deviation
        std_plot = std_dev_df.plot(x='wavelength', y=measuring_mode, kind='scatter', s=markersize, title = sample_name + " std dev", figsize = (8, 6))
        
        #save figures
        #pdf.savefig()
        #close plot
        #plt.close()
        
        #SAVE FILE
        #Convert to numpy
        average_np = average_df.to_numpy()
        std_dev_np = std_dev_df.to_numpy()
        
        #Create new folder
        avg_new_path = save_directory + "\\average\\"
        std_dev_new_path = save_directory + "\\std_dev\\"
        
        
        avg_new_path = os.path.join(save_directory , "average")
        std_dev_new_path = os.path.join(save_directory , "std_dev") 

        
        if not os.path.exists(avg_new_path):
            os.mkdir(avg_new_path)
        if not os.path.exists(std_dev_new_path):
            os.mkdir(std_dev_new_path)

        #creates new filename
        print(f"sample name: {sample_name}")

        new_avg_archive_name = os.path.join(avg_new_path, sample_name+'.txt')
        new_std_dev_archive_name = os.path.join( std_dev_new_path , sample_name+'.txt')

        #print(new_avg_archive_name)
        #saves files
        np.savetxt(new_avg_archive_name, average_np,fmt = "%.6f", delimiter="\t", header=metadata["header"], comments='')
        np.savetxt(new_std_dev_archive_name, std_dev_np,fmt = "%.6f", delimiter="\t", header=metadata["header"], comments='')
        #print("fin de la iteracion")

        def delete_blank_row(archive_name):
            with open(archive_name, "r") as f:
                data = f.read()
            with open(archive_name, "w") as f:
                f.write(data.replace("#DATA\n","#DATA"))

        delete_blank_row(new_avg_archive_name)
        delete_blank_row(new_std_dev_archive_name)
        

In [11]:
for folder in file_folder_data_path:
    
    jump_corrected_path = os.path.join(folder , "jump_corrected_files")
    report_path = os.path.join(folder, "report")
    
    code_set = get_files_with_same_name(jump_corrected_path)
    
    average_files(code_set, jump_corrected_path)
    

save_directory='C:\\Users\\EstebanSoto\\Downloads\\VINICIO\\VINICIO\\2023-03-CICIMAUCR-2-REFLECTANCE'
code='CICIMAUCR0108'
file='CICIMAUCR0001-1.txt'
      wavelength        %R
0         2500.0  3.463500
1         2499.0  3.416200
2         2498.0  3.524100
3         2497.0  3.399600
4         2496.0  3.417400
...          ...       ...
2246       254.0  2.849967
2247       253.0  2.845234
2248       252.0  2.883678
2249       251.0  2.857405
2250       250.0  2.868127

[2251 rows x 2 columns]
file='CICIMAUCR0001-2.txt'
      wavelength        %R
0         2500.0  9.186700
1         2499.0  9.122300
2         2498.0  9.092700
3         2497.0  9.165500
4         2496.0  9.198200
...          ...       ...
2246       254.0  5.702812
2247       253.0  5.670990
2248       252.0  5.701555
2249       251.0  5.721286
2250       250.0  5.731152

[2251 rows x 2 columns]
file='CICIMAUCR0001-3.txt'
      wavelength        %R
0         2500.0  8.556100
1         2499.0  8.439000
2         2498.0 

      wavelength         %R
0         2500.0  14.655200
1         2499.0  14.586100
2         2498.0  14.622700
3         2497.0  14.726000
4         2496.0  14.755600
...          ...        ...
2246       254.0   6.247295
2247       253.0   6.211405
2248       252.0   6.309065
2249       251.0   6.311188
2250       250.0   6.287228

[2251 rows x 2 columns]
file='CICIMAUCR0070-2.txt'
      wavelength         %R
0         2500.0  12.304200
1         2499.0  12.210300
2         2498.0  12.174500
3         2497.0  12.216800
4         2496.0  12.187800
...          ...        ...
2246       254.0   4.554454
2247       253.0   4.568200
2248       252.0   4.584017
2249       251.0   4.617158
2250       250.0   4.584865

[2251 rows x 2 columns]
file='CICIMAUCR0070-3.txt'
      wavelength         %R
0         2500.0  12.775000
1         2499.0  12.875500
2         2498.0  12.840400
3         2497.0  12.777200
4         2496.0  12.747900
...          ...        ...
2246       254.0   5.342256


      wavelength        %R
0         2500.0  4.738100
1         2499.0  4.861400
2         2498.0  4.792500
3         2497.0  4.771500
4         2496.0  4.687300
...          ...       ...
2246       254.0  5.813824
2247       253.0  5.807480
2248       252.0  5.822944
2249       251.0  5.851097
2250       250.0  5.853079

[2251 rows x 2 columns]
file='CICIMAUCR0116-1.txt'
      wavelength        %R
0         2500.0  4.461600
1         2499.0  4.536600
2         2498.0  4.433900
3         2497.0  4.455200
4         2496.0  4.600900
...          ...       ...
2246       254.0  5.799900
2247       253.0  5.751444
2248       252.0  5.771536
2249       251.0  5.813393
2250       250.0  5.803248

[2251 rows x 2 columns]
file='CICIMAUCR0141-1.txt'
      wavelength        %R
0         2500.0  6.635500
1         2499.0  6.665900
2         2498.0  6.638100
3         2497.0  6.629700
4         2496.0  6.621000
...          ...       ...
2246       254.0  5.999445
2247       253.0  6.075354
2248 

      wavelength        %R
0         2500.0  3.737500
1         2499.0  3.749100
2         2498.0  3.659500
3         2497.0  3.797300
4         2496.0  3.746100
...          ...       ...
2246       254.0  2.761045
2247       253.0  2.772335
2248       252.0  2.752102
2249       251.0  2.744724
2250       250.0  2.764286

[2251 rows x 2 columns]
file='CICIMAUCR0020-1.txt'
      wavelength        %R
0         2500.0  2.294900
1         2499.0  2.284600
2         2498.0  2.361600
3         2497.0  2.341600
4         2496.0  2.365700
...          ...       ...
2246       254.0  2.383049
2247       253.0  2.407033
2248       252.0  2.394119
2249       251.0  2.441869
2250       250.0  2.431993

[2251 rows x 2 columns]
file='CICIMAUCR0020-2.txt'
      wavelength        %R
0         2500.0  6.599700
1         2499.0  6.631600
2         2498.0  6.638600
3         2497.0  6.566400
4         2496.0  6.525800
...          ...       ...
2246       254.0  5.499290
2247       253.0  5.434925
2248 

      wavelength        %R
0         2500.0  3.855400
1         2499.0  3.992100
2         2498.0  4.021900
3         2497.0  3.941000
4         2496.0  3.890100
...          ...       ...
2246       254.0  5.125128
2247       253.0  5.099122
2248       252.0  5.163331
2249       251.0  5.140046
2250       250.0  5.185103

[2251 rows x 2 columns]
file='CICIMAUCR0006-3.txt'
      wavelength        %R
0         2500.0  6.153500
1         2499.0  6.070400
2         2498.0  6.213600
3         2497.0  6.170700
4         2496.0  6.130900
...          ...       ...
2246       254.0  4.502692
2247       253.0  4.550140
2248       252.0  4.531456
2249       251.0  4.526662
2250       250.0  4.511542

[2251 rows x 2 columns]
file='CICIMAUCR0008-1.txt'
      wavelength        %R
0         2500.0  2.410900
1         2499.0  2.379200
2         2498.0  2.513700
3         2497.0  2.457500
4         2496.0  2.413200
...          ...       ...
2246       254.0  2.730764
2247       253.0  2.717647
2248 

...

      wavelength        %R
0         2500.0  2.084600
1         2499.0  2.000200
2         2498.0  2.059600
3         2497.0  2.065100
4         2496.0  2.146500
...          ...       ...
2246       254.0  2.124762
2247       253.0  2.105032
2248       252.0  2.135195
2249       251.0  2.155958
2250       250.0  2.142116

[2251 rows x 2 columns]
file='BIOUCR0056-1.txt'
      wavelength        %R
0         2500.0  2.144100
1         2499.0  1.925800
2         2498.0  2.023600
3         2497.0  2.041400
4         2496.0  1.844200
...          ...       ...
2246       254.0  2.296645
2247       253.0  2.294067
2248       252.0  2.301491
2249       251.0  2.347998
2250       250.0  2.335830

[2251 rows x 2 columns]
file='BIOUCR0056-2.txt'
      wavelength        %R
0         2500.0  1.846800
1         2499.0  1.924500
2         2498.0  1.842300
3         2497.0  1.858700
4         2496.0  1.807400
...          ...       ...
2246       254.0  2.395238
2247       253.0  2.469240
2248       

      wavelength        %R
0         2500.0  3.175400
1         2499.0  3.149200
2         2498.0  3.152700
3         2497.0  3.188100
4         2496.0  3.092000
...          ...       ...
2246       254.0  2.235872
2247       253.0  2.214068
2248       252.0  2.222771
2249       251.0  2.218563
2250       250.0  2.245818

[2251 rows x 2 columns]
file='BIOUCR0011-3.txt'
      wavelength        %R
0         2500.0  3.305100
1         2499.0  3.359200
2         2498.0  3.427500
3         2497.0  3.438100
4         2496.0  3.325800
...          ...       ...
2246       254.0  1.970902
2247       253.0  1.998630
2248       252.0  2.021830
2249       251.0  2.006080
2250       250.0  2.007495

[2251 rows x 2 columns]
file='BIOUCR0012-1.txt'
      wavelength        %R
0         2500.0  3.512300
1         2499.0  3.512100
2         2498.0  3.532400
3         2497.0  3.505600
4         2496.0  3.527700
...          ...       ...
2246       254.0  2.173340
2247       253.0  2.170382
2248       

      wavelength        %R
0         2500.0  2.364500
1         2499.0  2.371900
2         2498.0  2.475000
3         2497.0  2.431100
4         2496.0  2.362000
...          ...       ...
2246       254.0  2.217528
2247       253.0  2.224356
2248       252.0  2.213410
2249       251.0  2.229378
2250       250.0  2.241529

[2251 rows x 2 columns]
file='BIOUCR0028-2.txt'
      wavelength        %R
0         2500.0  2.760500
1         2499.0  2.761800
2         2498.0  2.787100
3         2497.0  2.636000
4         2496.0  2.581900
...          ...       ...
2246       254.0  2.032268
2247       253.0  2.001832
2248       252.0  2.004913
2249       251.0  2.036469
2250       250.0  2.038616

[2251 rows x 2 columns]
file='BIOUCR0028-3.txt'
      wavelength        %R
0         2500.0  1.949100
1         2499.0  2.115000
2         2498.0  2.029500
3         2497.0  2.110500
4         2496.0  1.977100
...          ...       ...
2246       254.0  2.031996
2247       253.0  2.032807
2248       

      wavelength        %R
0         2500.0  2.608600
1         2499.0  2.472600
2         2498.0  2.527300
3         2497.0  2.396000
4         2496.0  2.502300
...          ...       ...
2246       254.0  2.419263
2247       253.0  2.360853
2248       252.0  2.410261
2249       251.0  2.418138
2250       250.0  2.404635

[2251 rows x 2 columns]
file='BIOUCR0044-2.txt'
      wavelength        %R
0         2500.0  2.146200
1         2499.0  2.211900
2         2498.0  2.128900
3         2497.0  2.224100
4         2496.0  2.219200
...          ...       ...
2246       254.0  1.778404
2247       253.0  1.779959
2248       252.0  1.768144
2249       251.0  1.800375
2250       250.0  1.818926

[2251 rows x 2 columns]
file='BIOUCR0044-3.txt'
      wavelength        %R
0         2500.0  2.206200
1         2499.0  2.271800
2         2498.0  2.219200
3         2497.0  2.171300
4         2496.0  2.213900
...          ...       ...
2246       254.0  1.887318
2247       253.0  1.884046
2248       

sample name: BIOUCR0056


\v